# Dreambooth
### Notebook implementation by Joe Penna (@MysteryGuitarM on Twitter) - Improvements by David Bielejeski
https://github.com/JoePenna/Dreambooth-Stable-Diffusion

### If on runpod / vast.ai / etc, spin up an A6000 or A100 pod using a Stable Diffusion template with Jupyter pre-installed.

## Build Environment

In [1]:
#BUILD ENV
!pip install omegaconf
!pip install einops
!pip install pytorch-lightning==1.6.5
!pip install test-tube
!pip install transformers
!pip install kornia
!pip install -e git+https://github.com/CompVis/taming-transformers.git@master#egg=taming-transformers
!pip install -e git+https://github.com/openai/CLIP.git@main#egg=clip
!pip install setuptools==59.5.0
!pip install pillow==9.0.1
!pip install torchmetrics==0.6.0
!pip install -e .
!pip install protobuf==3.20.1
!pip install gdown
!pip install pydrive
!pip install -qq diffusers["training"]==0.3.0 transformers ftfy
!pip install -qq "ipywidgets>=7,<8"
!pip install huggingface_hub
!pip install ipywidgets

     |████████████████████████████████| 79 kB 11.7 MB/s eta 0:00:01
     |████████████████████████████████| 117 kB 46.3 MB/s eta 0:00:01
  Created wheel for antlr4-python3-runtime: filename=antlr4_python3_runtime-4.9.3-py3-none-any.whl size=144575 sha256=025522eacd9b176186009613779d0829446aaf3442d4f609cf01b0b7d40ab006
  Stored in directory: /root/.cache/pip/wheels/8b/8d/53/2af8772d9aec614e3fc65e53d4a993ad73c61daa8bbd85a873
Successfully built antlr4-python3-runtime
     |████████████████████████████████| 585 kB 19.6 MB/s eta 0:00:01
     |████████████████████████████████| 1.0 MB 93.9 MB/s eta 0:00:01
     |████████████████████████████████| 140 kB 82.8 MB/s eta 0:00:01
     |████████████████████████████████| 419 kB 52.1 MB/s eta 0:00:01
     |████████████████████████████████| 5.9 MB 7.3 MB/s eta 0:00:01
     |████████████████████████████████| 948 kB 58.0 MB/s eta 0:00:01
     |████████████████████████████████| 148 kB 81.4 MB/s eta 0:00:01
     |████████████████████████████████| 94 kB 4.1

In [2]:
## Move the sd-v1-4.ckpt to the root of this directory as "model.ckpt"
#actual_locations_of_model_blob = !readlink -f {downloaded_model_path}
#!cp {actual_locations_of_model_blob[-1]} model.ckpt
!wget 'https://prodesk.home.thijn.ovh/sd-v1-4.ckpt'
!cp sd-v1-4.ckpt model.ckpt

Hit:1 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:2 http://security.ubuntu.com/ubuntu bionic-security InRelease
Hit:3 http://archive.ubuntu.com/ubuntu bionic-updates InRelease
Hit:4 http://archive.ubuntu.com/ubuntu bionic-backports InRelease
Reading package lists... Done
Reading package lists... Done
Building dependency tree       
Reading state information... Done
wget is already the newest version (1.19.4-1ubuntu2.2).
0 upgraded, 0 newly installed, 0 to remove and 19 not upgraded.
--2022-09-29 13:08:34--  https://prodesk.home.thijn.ovh/sd-v1-4.ckpt
Resolving prodesk.home.thijn.ovh (prodesk.home.thijn.ovh)... 84.245.9.220
Connecting to prodesk.home.thijn.ovh (prodesk.home.thijn.ovh)|84.245.9.220|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4265380512 (4.0G) [application/octet-stream]
Saving to: ‘sd-v1-4.ckpt’

sd-v1-4.ckpt        100%[===================>]   3.97G  63.1MB/s    in 56s     

2022-09-29 13:09:30 (72.9 MB/s) - ‘sd-v1-4.ckpt’ saved [4

## Download pre-generated regularization images

We've created the following image sets

* man_euler - provided by Niko Pueringer (Corridor Digital) - euler @ 40 steps, CFG 7.5
* man_unsplash - pictures from various photographers
* person_ddim
* woman_ddim - provided by David Bielejeski - ddim @ 50 steps, CFG 10.0

`person_ddim` is recommended

In [3]:
# Grab the existing regularization images
# Choose the dataset that best represents what you are trying to do and matches what you used for your token
# man_euler, man_unsplash, person_ddim, woman_ddim
dataset="person_ddim"
!rm -rf Stable-Diffusion-Regularization-Images-{dataset}
!git clone https://github.com/djbielejeski/Stable-Diffusion-Regularization-Images-{dataset}.git

!mkdir -p outputs/txt2img-samples/samples/{dataset}
!mv -v Stable-Diffusion-Regularization-Images-{dataset}/{dataset}/*.* outputs/txt2img-samples/samples/{dataset}

Cloning into 'Stable-Diffusion-Regularization-Images-person_ddim'...
remote: Enumerating objects: 1503, done.
remote: Total 1503 (delta 0), reused 0 (delta 0), pack-reused 1503
Receiving objects: 100% (1503/1503), 657.41 MiB | 9.23 MiB/s, done.
Checking out files: 100% (1500/1500), done.
renamed 'Stable-Diffusion-Regularization-Images-person_ddim/person_ddim/person_ddim_00000.png' -> 'outputs/txt2img-samples/samples/person_ddim/person_ddim_00000.png'
renamed 'Stable-Diffusion-Regularization-Images-person_ddim/person_ddim/person_ddim_00001.png' -> 'outputs/txt2img-samples/samples/person_ddim/person_ddim_00001.png'
renamed 'Stable-Diffusion-Regularization-Images-person_ddim/person_ddim/person_ddim_00002.png' -> 'outputs/txt2img-samples/samples/person_ddim/person_ddim_00002.png'
renamed 'Stable-Diffusion-Regularization-Images-person_ddim/person_ddim/person_ddim_00003.png' -> 'outputs/txt2img-samples/samples/person_ddim/person_ddim_00003.png'
renamed 'Stable-Diffusion-Regularization-Images

# Upload your training images
Upload 10-20 images of someone to

```
/workspace/Dreambooth-Stable-Diffusion/training_samples
```

WARNING: Be sure to upload an *even* amount of images, otherwise the training inexplicably stops at 1500 steps.

*   2-3 full body
*   3-5 upper body 
*   5-12 close-up on face

In [4]:
#@markdown Add here the URLs to the images of the concept you are adding
urls = [
"https://prodesk.home.thijn.ovh/thijn/IMG_0133.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0134.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0135.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0136.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0137.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0138.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0139.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0140.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0141.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0142.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0143.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0144.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0145.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0146.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0147.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0148.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0149.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0150.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0151.png",
"https://prodesk.home.thijn.ovh/thijn/IMG_0152.png"
 ## You can add additional images here
]

In [6]:
#@title Download and check the images you have just added
import os
import requests
from io import BytesIO
from PIL import Image


def image_grid(imgs, rows, cols):
 assert len(imgs) == rows*cols

 w, h = imgs[0].size
 grid = Image.new('RGB', size=(cols*w, rows*h))
 grid_w, grid_h = grid.size

 for i, img in enumerate(imgs):
  grid.paste(img, box=(i%cols*w, i//cols*h))
 return grid

def download_image(url):
 try:
  response = requests.get(url)
 except:
  return None
 return Image.open(BytesIO(response.content)).convert("RGB")

images = list(filter(None,[download_image(url) for url in urls]))
save_path = "./training_samples"
if not os.path.exists(save_path):
 os.mkdir(save_path)
[image.save(f"{save_path}/{i}.png", format="png") for i, image in enumerate(images)]


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]

## Training

If training a person or subject, keep an eye on your project's `logs/{folder}/images/train/samples_scaled_gs-00xxxx` generations.

If training a style, keep an eye on your project's `logs/{folder}/images/train/samples_gs-00xxxx` generations.

In [7]:
# START THE TRAINING
project_name = "thijngeurts"
batch_size = 1000
class_word = "person"  # << match this word to the class word from regularization images above
reg_data_root = "/workspace/Dreambooth-Stable-Diffusion/outputs/txt2img-samples/samples/" + dataset

!rm -rf training_samples/.ipynb_checkpoints
!python "main.py" \
 --base configs/stable-diffusion/v1-finetune_unfrozen.yaml \
 -t \
 --actual_resume "model.ckpt" \
 --reg_data_root {reg_data_root} \
 -n {project_name} \
 --gpus 0, \
 --data_root "/workspace/Dreambooth-Stable-Diffusion/training_samples" \
 --batch_size {batch_size} \
 --class_word class_word

Global seed set to 23
Running on GPUs 0,
Loading model from model.ckpt
LatentDiffusion: Running in eps-prediction mode
DiffusionWrapper has 859.52 M params.
making attention of type 'vanilla' with 512 in_channels
Working with z of shape (1, 4, 64, 64) = 16384 dimensions.
making attention of type 'vanilla' with 512 in_channels
Downloading: 100%|███████████████████████████| 961k/961k [00:00<00:00, 1.50MB/s]
Downloading: 100%|███████████████████████████| 525k/525k [00:00<00:00, 1.06MB/s]
Downloading: 100%|█████████████████████████████| 905/905 [00:00<00:00, 2.32MB/s]
Downloading: 100%|█████████████████████████| 4.52k/4.52k [00:00<00:00, 4.20MB/s]
Downloading: 100%|█████████████████████████| 1.71G/1.71G [00:18<00:00, 90.4MB/s]
Some weights of the model checkpoint at openai/clip-vit-large-patch14 were not used when initializing CLIPTextModel: ['vision_model.encoder.layers.7.layer_norm2.weight', 'vision_model.encoder.layers.5.mlp.fc2.bias', 'vision_model.encoder.layers.2.mlp.fc1.bias', 'visi

## Pruning (12GB to 2GB)
We are working on having this happen automatically (TODO: PR's welcome)

In [8]:
directory_paths = !ls -d logs/*

In [9]:
# This version should automatically prune around 10GB from the ckpt file
last_checkpoint_file = directory_paths[-1] + "/checkpoints/last.ckpt"
!python "scripts/prune-ckpt.py" --ckpt {last_checkpoint_file}

prunin' in path: logs/training_samples2022-09-29T13-19-41_thijngeurts/checkpoints/last.ckpt
dict_keys(['epoch', 'global_step', 'pytorch-lightning_version', 'state_dict', 'loops', 'callbacks', 'optimizer_states', 'lr_schedulers'])
removing optimizer states for path logs/training_samples2022-09-29T13-19-41_thijngeurts/checkpoints/last.ckpt
This is global step 2000.
saving pruned checkpoint at: logs/training_samples2022-09-29T13-19-41_thijngeurts/checkpoints/last-pruned.ckpt
New ckpt size: 2.13 GB. Saved 9.99 GB by removing optimizer states


In [10]:
last_checkpoint_file_pruned = directory_paths[-1] + "/checkpoints/last-pruned.ckpt"
training_samples = !ls training_samples
date_string = !date +"%Y-%m-%dT%H-%M-%S"
file_name = date_string[-1] + "_" + project_name + "_" + str(len(training_samples)) + "_training_images_" +  str(batch_size) + "_batch_size_" + class_word + "_class_word.ckpt"
!mkdir -p trained_models
!mv {last_checkpoint_file_pruned} trained_models/{file_name}

In [14]:
# Download your trained model file from `trained_models` and use in your favorite Stable Diffusion repo!
!wget -nc 'https://prodesk.home.thijn.ovh/gijs/ai'
!chmod 600 ai
!scp -r -i ai -P 2387 -o StrictHostKeyChecking=no ./trained_models ai@home.thijn.ovh:/mnt/hdd/ai/

File ‘ai’ already there; not retrieving.

2022-09-29T14-15-55_thijngeurts_20_training_i 100% 2034MB  48.7MB/s   00:41    


## Generate Images With Your Trained Model!

In [ ]:
!python scripts/stable_txt2img.py \
 --ddim_eta 0.0 \
 --n_samples 1 \
 --n_iter 10 \
 --scale 7.0 \
 --ddim_steps 50 \
 --ckpt "/workspace/Dreambooth-Stable-Diffusion/trained_models/2022-09-29T14-15-55_thijngeurts_20_training_images_1000_batch_size_person_class_word.ckpt" \
 --prompt "beautiful oil painting of thijngeurts with high detail of a gorgeous wood-elf ranger from dungeons and dragons in the desert by artgerm and greg rutkowski and thomas kinkade"

Global seed set to 42
Loading model from /workspace/Dreambooth-Stable-Diffusion/trained_models/2022-09-29T14-15-55_thijngeurts_20_training_images_1000_batch_size_person_class_word.ckpt
Global Step: 2000
LatentDiffusion: Running in eps-prediction mode
DiffusionWrapper has 859.52 M params.
making attention of type 'vanilla' with 512 in_channels
Working with z of shape (1, 4, 32, 32) = 4096 dimensions.
making attention of type 'vanilla' with 512 in_channels
Some weights of the model checkpoint at openai/clip-vit-large-patch14 were not used when initializing CLIPTextModel: ['vision_model.encoder.layers.12.self_attn.q_proj.weight', 'vision_model.encoder.layers.21.mlp.fc1.bias', 'vision_model.encoder.layers.0.mlp.fc2.bias', 'vision_model.encoder.layers.11.mlp.fc2.bias', 'vision_model.encoder.layers.0.mlp.fc2.weight', 'vision_model.encoder.layers.19.self_attn.out_proj.weight', 'vision_model.encoder.layers.15.mlp.fc2.bias', 'vision_model.encoder.layers.22.self_attn.k_proj.weight', 'vision_mode